In [149]:
# upgrade in command line for specific interpreter

import sys
sys.executable
# /Users/lianfeng/Document/species_richness_sdm/venv/bin/pip install --upgrade tensorflow

'/Users/lianfeng/miniconda3/envs/tf/bin/python'

In [150]:
# 
exec('from __future__ import absolute_import, division, print_function, unicode_literals')

import numpy as np
import datetime
import pathlib
from sqlalchemy import create_engine
import matplotlib.pyplot as plt
import pandas as pd
import seaborn as sns
from sklearn.model_selection import train_test_split
from sklearn import preprocessing
from sklearn.preprocessing import MinMaxScaler
from sklearn.impute import KNNImputer

from tensorflow import keras
from tensorflow.keras import layers
from tensorflow.keras.layers import Dense, Activation, Dropout

In [151]:
from hyperopt import Trials, STATUS_OK, tpe
from hyperas import optim
from hyperas.distributions import choice, uniform

In [160]:
def data():
    localhost = {'user': 'postgres', 'password': 'postgres', 'host': 'localhost', 'port': 5432, 'db': 'fiadb'}
    params = 'postgresql://{0}:{1}@{2}:{3}/{4}'
    engine = create_engine(params.format(localhost['user'], localhost['password'], localhost['host'], localhost['port'], localhost['db']))
    pergrid_base = """select distinct * from predictor.pergrid_base"""
    pergrid_base_df = pd.read_sql(pergrid_base, engine)

    # separate predictor variables from outcome varaible
    y = pergrid_base_df['tsr']
    grid_id = pergrid_base_df['grid_id']
    pred_var= ['aet', 'ai', 'art', 'ewd', 'fa', 'map', 'mat', 'mpdq',
           'mtcq', 'pet', 'psn', 'ra', 'rmap', 'rmat', 'tsn', 'mfdf', 'alt','shg','mtwq','wa']
    pergrid_base_pred_df = pergrid_base_df[pred_var]

    # fill NaN with values from neighbor pixels
    imputer = KNNImputer(n_neighbors=5)
    pergrid_base_filled = imputer.fit_transform(pergrid_base_pred_df)
    pergrid_base_df = pd.DataFrame(pergrid_base_filled)
    pergrid_base_df.head()

    ss = MinMaxScaler()
    X_std = ss.fit_transform(pergrid_base_df)

    Xstd=pd.DataFrame(data=X_std[0:,0:],
                    index=pergrid_base_pred_df.index,
                    columns=pred_var)

    x_train, x_test, y_train, y_test = train_test_split(Xstd, y, test_size=0.1, random_state=12345)
    x_train, x_val, y_train, y_val = train_test_split(x_train, y_train, test_size=0.1, random_state=12345)

    return x_train, x_val, x_test, y_train, y_val, y_test

In [161]:
X_train, X_val, X_test, Y_train, Y_val, Y_test = data()

In [162]:
def create_model(x_train, y_train, x_val, y_val):

    model = keras.Sequential()
    model.add(layers.Dense({{choice([256, 512, 1024])}}, input_shape=(x_train.shape[1],)))  # tune # of units
    model.add(Activation({{choice(['relu'])}}))  # tune the activation function
    model.add(Dropout({{uniform(0, 1)}}))  # tune dropout rate

    model.add(Dense({{choice([256, 512, 1024])}}))
    model.add(Activation({{choice(['relu'])}}))
    model.add(Dropout({{uniform(0, 1)}}))
    
    model.add(Dense({{choice([256, 512, 1024])}}))
    model.add(Activation({{choice(['relu'])}}))
    model.add(Dropout({{uniform(0, 1)}}))

    # tune # of layers
    if {{choice(['three', 'four'])}} == 'four':
        model.add(Dense({{choice([256, 512, 1024])}}))
        model.add(Activation({{choice(['relu'])}}))
        model.add(Dropout({{uniform(0, 1)}}))

    model.add(Dense(1))
    model.add(Activation('linear'))

    # tune the optimizer and the learning rate
    adam = keras.optimizers.Adam(lr={{choice([10 ** -4, 10 ** -3, 10 ** -2])}})
    rmsprop = keras.optimizers.RMSprop(lr={{choice([10 ** -3, 10 ** -2, 10 ** -1])}})
    sgd = keras.optimizers.SGD(lr={{choice([10 ** -3, 10 ** -2, 10 ** -1])}})

    choiceval = {{choice(['adam', 'sgd', 'rmsprop'])}}
    if choiceval == 'adam':
        optim = adam
    elif choiceval == 'rmsprop':
        optim = rmsprop
    else:
        optim = sgd

    model.compile(loss='mae', metrics=['mean_absolute_error'], optimizer=optim)
    result=model.fit(x_train, y_train,
              batch_size={{choice([128, 256, 512])}},
              epochs=1000,
              verbose=2,
              validation_data=(x_val, y_val))
    
    mae, mse = model.evaluate(x_val, y_val, verbose=0)
    return {'loss': mae, 'status': STATUS_OK, 'model': model}

In [163]:
best_run, best_model = optim.minimize(model=create_model,
                                      data=data,
                                      algo=tpe.suggest,
                                      max_evals=30,
                                      trials=Trials(),
                                      notebook_name='ffnn')

>>> Imports:
#coding=utf-8

try:
    import sys
except:
    pass

try:
    import numpy as np
except:
    pass

try:
    import datetime
except:
    pass

try:
    import pathlib
except:
    pass

try:
    from sqlalchemy import create_engine
except:
    pass

try:
    import matplotlib.pyplot as plt
except:
    pass

try:
    import pandas as pd
except:
    pass

try:
    import seaborn as sns
except:
    pass

try:
    from sklearn.model_selection import train_test_split
except:
    pass

try:
    from sklearn import preprocessing
except:
    pass

try:
    from sklearn.preprocessing import MinMaxScaler
except:
    pass

try:
    from sklearn.impute import KNNImputer
except:
    pass

try:
    from tensorflow import keras
except:
    pass

try:
    from tensorflow.keras import layers
except:
    pass

try:
    from tensorflow.keras.layers import Dense, Activation, Dropout
except:
    pass

try:
    from hyperopt import Trials, STATUS_OK, tpe
except:
    pass

try:
    from hyperas im

Epoch 60/1000                                         
12401/12401 - 2s - loss: 3.3608 - mean_absolute_error: 3.3608 - val_loss: 3.2492 - val_mean_absolute_error: 3.2492

Epoch 61/1000                                         
12401/12401 - 2s - loss: 3.3543 - mean_absolute_error: 3.3543 - val_loss: 3.2043 - val_mean_absolute_error: 3.2043

Epoch 62/1000                                         
12401/12401 - 2s - loss: 3.3505 - mean_absolute_error: 3.3505 - val_loss: 3.2840 - val_mean_absolute_error: 3.2840

Epoch 63/1000                                         
12401/12401 - 2s - loss: 3.3545 - mean_absolute_error: 3.3545 - val_loss: 3.3310 - val_mean_absolute_error: 3.3310

Epoch 64/1000                                         
12401/12401 - 2s - loss: 3.3502 - mean_absolute_error: 3.3502 - val_loss: 3.2432 - val_mean_absolute_error: 3.2432

Epoch 65/1000                                         
12401/12401 - 2s - loss: 3.3058 - mean_absolute_error: 3.3058 - val_loss: 3.2905 - val_mea

Epoch 108/1000                                        
12401/12401 - 2s - loss: 3.2173 - mean_absolute_error: 3.2173 - val_loss: 3.2473 - val_mean_absolute_error: 3.2473

Epoch 109/1000                                        
12401/12401 - 2s - loss: 3.2108 - mean_absolute_error: 3.2108 - val_loss: 3.2511 - val_mean_absolute_error: 3.2511

Epoch 110/1000                                        
12401/12401 - 2s - loss: 3.2214 - mean_absolute_error: 3.2214 - val_loss: 3.3557 - val_mean_absolute_error: 3.3557

Epoch 111/1000                                        
12401/12401 - 2s - loss: 3.1999 - mean_absolute_error: 3.1999 - val_loss: 3.1672 - val_mean_absolute_error: 3.1672

Epoch 112/1000                                        
12401/12401 - 2s - loss: 3.2356 - mean_absolute_error: 3.2356 - val_loss: 3.3765 - val_mean_absolute_error: 3.3765

Epoch 113/1000                                        
12401/12401 - 2s - loss: 3.2121 - mean_absolute_error: 3.2121 - val_loss: 3.1984 - val_mea

Epoch 156/1000                                        
12401/12401 - 2s - loss: 3.1548 - mean_absolute_error: 3.1548 - val_loss: 3.2996 - val_mean_absolute_error: 3.2996

Epoch 157/1000                                        
12401/12401 - 2s - loss: 3.1368 - mean_absolute_error: 3.1368 - val_loss: 3.2215 - val_mean_absolute_error: 3.2215

Epoch 158/1000                                        
12401/12401 - 2s - loss: 3.1261 - mean_absolute_error: 3.1261 - val_loss: 3.2904 - val_mean_absolute_error: 3.2904

Epoch 159/1000                                        
12401/12401 - 2s - loss: 3.1162 - mean_absolute_error: 3.1162 - val_loss: 3.2635 - val_mean_absolute_error: 3.2635

Epoch 160/1000                                        
12401/12401 - 2s - loss: 3.1313 - mean_absolute_error: 3.1313 - val_loss: 3.0939 - val_mean_absolute_error: 3.0939

Epoch 161/1000                                        
12401/12401 - 2s - loss: 3.1061 - mean_absolute_error: 3.1061 - val_loss: 3.1033 - val_mea

Epoch 204/1000                                        
12401/12401 - 2s - loss: 3.0790 - mean_absolute_error: 3.0790 - val_loss: 3.2858 - val_mean_absolute_error: 3.2858

Epoch 205/1000                                        
12401/12401 - 2s - loss: 3.0528 - mean_absolute_error: 3.0528 - val_loss: 3.0595 - val_mean_absolute_error: 3.0595

Epoch 206/1000                                        
12401/12401 - 2s - loss: 3.0567 - mean_absolute_error: 3.0567 - val_loss: 3.0859 - val_mean_absolute_error: 3.0859

Epoch 207/1000                                        
12401/12401 - 2s - loss: 3.0844 - mean_absolute_error: 3.0844 - val_loss: 3.0949 - val_mean_absolute_error: 3.0949

Epoch 208/1000                                        
12401/12401 - 2s - loss: 3.0748 - mean_absolute_error: 3.0748 - val_loss: 3.1161 - val_mean_absolute_error: 3.1161

Epoch 209/1000                                        
12401/12401 - 2s - loss: 3.0807 - mean_absolute_error: 3.0807 - val_loss: 3.0824 - val_mea

...

Epoch 644/1000                                                                        
12401/12401 - 2s - loss: 2.7217 - mean_absolute_error: 2.7217 - val_loss: 2.9772 - val_mean_absolute_error: 2.9772

Epoch 645/1000                                                                        
12401/12401 - 2s - loss: 2.6998 - mean_absolute_error: 2.6998 - val_loss: 3.0340 - val_mean_absolute_error: 3.0340

Epoch 646/1000                                                                        
12401/12401 - 2s - loss: 2.7013 - mean_absolute_error: 2.7013 - val_loss: 2.9410 - val_mean_absolute_error: 2.9410

Epoch 647/1000                                                                        
12401/12401 - 2s - loss: 2.6891 - mean_absolute_error: 2.6891 - val_loss: 3.1258 - val_mean_absolute_error: 3.1258

Epoch 648/1000                                                                        
12401/12401 - 2s - loss: 2.6742 - mean_absolute_error: 2.6742 - val_loss: 3.0164 - val_mean_absolute_

Epoch 724/1000                                                                        
12401/12401 - 2s - loss: 2.6438 - mean_absolute_error: 2.6438 - val_loss: 3.0089 - val_mean_absolute_error: 3.0089

Epoch 725/1000                                                                        
12401/12401 - 2s - loss: 2.6422 - mean_absolute_error: 2.6423 - val_loss: 3.0699 - val_mean_absolute_error: 3.0699

Epoch 726/1000                                                                        
12401/12401 - 2s - loss: 2.6758 - mean_absolute_error: 2.6758 - val_loss: 3.0457 - val_mean_absolute_error: 3.0457

Epoch 727/1000                                                                        
12401/12401 - 2s - loss: 2.6371 - mean_absolute_error: 2.6371 - val_loss: 3.0050 - val_mean_absolute_error: 3.0050

Epoch 728/1000                                                                        
12401/12401 - 2s - loss: 2.6536 - mean_absolute_error: 2.6536 - val_loss: 2.9837 - val_mean_absolute_

Epoch 804/1000                                                                        
12401/12401 - 2s - loss: 2.6624 - mean_absolute_error: 2.6624 - val_loss: 2.9361 - val_mean_absolute_error: 2.9361

Epoch 805/1000                                                                        
12401/12401 - 2s - loss: 2.6468 - mean_absolute_error: 2.6468 - val_loss: 2.9980 - val_mean_absolute_error: 2.9980

Epoch 806/1000                                                                        
12401/12401 - 2s - loss: 2.6463 - mean_absolute_error: 2.6463 - val_loss: 3.0279 - val_mean_absolute_error: 3.0279

Epoch 807/1000                                                                        
12401/12401 - 2s - loss: 2.6206 - mean_absolute_error: 2.6206 - val_loss: 2.9507 - val_mean_absolute_error: 2.9507

Epoch 808/1000                                                                        
12401/12401 - 2s - loss: 2.6297 - mean_absolute_error: 2.6297 - val_loss: 2.9888 - val_mean_absolute_

Epoch 884/1000                                                                        
12401/12401 - 2s - loss: 2.5631 - mean_absolute_error: 2.5631 - val_loss: 3.0074 - val_mean_absolute_error: 3.0074

Epoch 885/1000                                                                        
12401/12401 - 2s - loss: 2.5924 - mean_absolute_error: 2.5924 - val_loss: 3.0389 - val_mean_absolute_error: 3.0389

Epoch 886/1000                                                                        
12401/12401 - 2s - loss: 2.6015 - mean_absolute_error: 2.6015 - val_loss: 2.9667 - val_mean_absolute_error: 2.9667

Epoch 887/1000                                                                        
12401/12401 - 2s - loss: 2.6085 - mean_absolute_error: 2.6085 - val_loss: 2.9493 - val_mean_absolute_error: 2.9493

Epoch 888/1000                                                                        
12401/12401 - 2s - loss: 2.5933 - mean_absolute_error: 2.5933 - val_loss: 3.0250 - val_mean_absolute_

Epoch 964/1000                                                                        
12401/12401 - 2s - loss: 2.5474 - mean_absolute_error: 2.5474 - val_loss: 3.0867 - val_mean_absolute_error: 3.0867

Epoch 965/1000                                                                        
12401/12401 - 2s - loss: 2.5438 - mean_absolute_error: 2.5438 - val_loss: 2.9478 - val_mean_absolute_error: 2.9478

Epoch 966/1000                                                                        
12401/12401 - 2s - loss: 2.5794 - mean_absolute_error: 2.5794 - val_loss: 3.0268 - val_mean_absolute_error: 3.0268

Epoch 967/1000                                                                        
12401/12401 - 2s - loss: 2.5447 - mean_absolute_error: 2.5447 - val_loss: 3.0333 - val_mean_absolute_error: 3.0333

Epoch 968/1000                                                                        
12401/12401 - 2s - loss: 2.5659 - mean_absolute_error: 2.5659 - val_loss: 2.9834 - val_mean_absolute_

In [164]:
print(best_run)

{'Activation': 0, 'Activation_1': 0, 'Activation_2': 0, 'Activation_3': 0, 'Dense': 2, 'Dense_1': 0, 'Dense_2': 1, 'Dense_3': 2, 'Dropout': 0.21851337568749496, 'Dropout_1': 0.06592681764329411, 'Dropout_2': 0.5788302926379603, 'Dropout_3': 0, 'Dropout_4': 0.31899443452607434, 'batch_size': 1, 'choiceval': 2, 'choiceval_1': 0, 'lr': 0, 'lr_1': 0, 'lr_2': 1}


In [165]:
X_train, X_val, X_test, Y_train, Y_val, Y_test = data()

In [166]:
best_model.evaluate(X_test, Y_test, verbose=0)

[2.8511445868023078, 2.8511448]

In [167]:
best_model.summary()

Model: "sequential_109"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_467 (Dense)            (None, 1024)              21504     
_________________________________________________________________
activation_467 (Activation)  (None, 1024)              0         
_________________________________________________________________
dropout_358 (Dropout)        (None, 1024)              0         
_________________________________________________________________
dense_468 (Dense)            (None, 256)               262400    
_________________________________________________________________
activation_468 (Activation)  (None, 256)               0         
_________________________________________________________________
dropout_359 (Dropout)        (None, 256)               0         
_________________________________________________________________
dense_469 (Dense)            (None, 512)            

### Evaluation Metrics

In [168]:
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import r2_score

In [169]:
best_model.predict(X_train)

array([[20.248089],
       [26.534554],
       [23.471634],
       ...,
       [22.37674 ],
       [21.780334],
       [25.458702]], dtype=float32)

In [170]:
Y_train

1751     19.0
12883    28.0
10125    29.0
1722     39.0
14401     1.0
         ... 
12255     5.0
5694      1.0
9869     26.0
14316    28.0
12598    24.0
Name: tsr, Length: 12401, dtype: float64

In [171]:
Y_train_pred = best_model.predict(X_train).flatten()
print('train MAE', mean_absolute_error(Y_train_pred, Y_train))
print('train r2', r2_score(Y_train, Y_train_pred))

train MAE 2.505091583975841
train r2 0.9175891299488492


In [172]:
Y_test_pred = best_model.predict(X_test).flatten()
print('test MAE', mean_absolute_error(Y_test_pred, Y_test))
print('test r2', r2_score(Y_test, Y_test_pred))

test MAE 2.8511446067354087
test r2 0.907375693004244


In [173]:
ffnn_y_test = pd.DataFrame(
    {'tsr': Y_test,
     'tsr_predicted': Y_test_pred})
ffnn_y_test.to_sql(name='ffnn_y_test', con=engine, schema='predictor', if_exists='replace', index=False)

### Make TSR predictions using the full dataset

In [174]:
localhost = {'user': 'postgres', 'password': 'postgres', 'host': 'localhost', 'port': 5432, 'db': 'fiadb'}
params = 'postgresql://{0}:{1}@{2}:{3}/{4}'
engine = create_engine(params.format(localhost['user'], localhost['password'], localhost['host'], localhost['port'], localhost['db']))
pergrid_base = """select distinct * from predictor.pergrid_base"""
pergrid_base_df = pd.read_sql(pergrid_base, engine)

# separate predictor variables from outcome varaible
y = pergrid_base_df['tsr']
grid_id = pergrid_base_df['grid_id']
pred_var= ['aet', 'ai', 'art', 'ewd', 'fa', 'map', 'mat', 'mpdq',
       'mtcq', 'pet', 'psn', 'ra', 'rmap', 'rmat', 'tsn', 'mfdf', 'alt','shg','mtwq','wa']
pergrid_base_pred_df = pergrid_base_df[pred_var]

# fill NaN with values from neighbor pixels
imputer = KNNImputer(n_neighbors=5)
pergrid_base_filled = imputer.fit_transform(pergrid_base_pred_df)
pergrid_base_df = pd.DataFrame(pergrid_base_filled)
pergrid_base_df.head()

ss = MinMaxScaler()
X_std = ss.fit_transform(pergrid_base_df)

Xstd=pd.DataFrame(data=X_std[0:,0:],
                index=pergrid_base_pred_df.index,
                columns=pred_var)

In [177]:
# test_predictions = model.predict(normed_test_data).flatten()
y_pred = best_model.predict(Xstd).flatten()

### Ingest TSR predictions to PG

In [178]:
pergrid_all_predicted = pd.DataFrame(
    {'grid_id': grid_id,
     'tsr': y,
     'tsr_predicted': y_pred})

In [179]:
pergrid_all_predicted.head()

grid_id  tsr  tsr_predicted
0      110  4.0       1.843237
1      111  2.0       2.252534
2      195  5.0       4.105301
3      337  1.0       1.722340
4      338  1.0       1.841481

In [180]:
pergrid_all_predicted.to_sql(name='ffnn', con=engine, schema='predictor', if_exists='replace', index=False)

/Users/lianfeng/miniconda3/envs/tf/lib/python3.7/site-packages/sqlalchemy/dialects/postgresql/base.py:3087: SAWarning: Did not recognize type 'geometry' of column 'wkb_geometry'
  "Did not recognize type '%s' of column '%s'" % (attype, name)


In [181]:
update_geom = """
alter table predictor.ffnn add column if not exists wkb_geometry geometry(Polygon,4269);
update predictor.ffnn A SET wkb_geometry = B.wkb_geometry
FROM predictor.pergrid_base B
WHERE A.grid_id = B.grid_id
"""

In [182]:
connection = engine.connect()
connection.execute(update_geom)

In [183]:
update_residual = """
alter table predictor.ffnn add column residual double precision;
update predictor.ffnn set residual = (tsr_predicted-tsr);
"""

In [184]:
connection = engine.connect()
connection.execute(update_residual)